In [1]:
# necessary packages #

#using Pkg
#Pkg.add("Distances")
using Distributions
using Random
using Distances
using LinearAlgebra
using SparseArrays
using IterativeSolvers
using ProgressMeter
using JLD2
using DataFrames

In [2]:
include("../../../util2.j")

colnorm (generic function with 1 method)

In [3]:
# unnecessary packages #

#using Pkg
#Pkg.add("UnicodePlots")
using UnicodePlots   # check the structure of the sparse matrix
using BenchmarkTools

using StatsPlots
using MCMCChains
using PrettyTables

In [4]:
Sys.free_memory()/(2^20*1024)

21.568153381347656

In [5]:
@time @load "../../data/LMC_data/LMC_data_small_expanded.jld";

  2.482012 seconds (6.41 M allocations: 688.232 MiB, 17.04% gc time)


In [6]:
using RData
@time data_cleaned = load("../../data/rawdata/data_cleaned_small_expanded.RData", convert = true)["data_cleaned_small"];
@time hold_index_set = load("../../data/rawdata/hold_index_small_expanded.RData", convert = true);

  9.038187 seconds (33.27 M allocations: 2.082 GiB, 10.85% gc time)
  0.067664 seconds (49.88 k allocations: 7.060 MiB)


In [7]:
# pick response NDVI and EVI
# pick explanatory variables 12 to 24, no 16
DataFrames.describe(data_cleaned)

28×8 DataFrame. Omitted printing of 5 columns
│ Row │ variable                        │ mean       │ min         │
│     │ Symbol                          │ Float64    │ Float64     │
├─────┼─────────────────────────────────┼────────────┼─────────────┤
│ 1   │ x                               │ -1.04265e7 │ -1.11193e7  │
│ 2   │ y                               │ 3.83786e6  │ 3.33608e6   │
│ 3   │ scaled_x                        │ 0.6928     │ 0.0         │
│ 4   │ scaled_y                        │ 0.501779   │ 0.0         │
│ 5   │ NDVI                            │ 0.240122   │ -0.00954541 │
│ 6   │ EVI                             │ 0.150172   │ -0.00400802 │
│ 7   │ red_reflectance                 │ 0.144424   │ 0.0047      │
│ 8   │ NIR_reflectance                 │ 0.243485   │ 0.0116      │
│ 9   │ blue_reflectance                │ 0.0752273  │ 0.0001      │
│ 10  │ MIR_reflectance                 │ 0.224949   │ 0.0016      │
⋮
│ 18  │ ET                              │ 1.33848    │ -0.798508   │
│ 19  │ PLE                             │ 1.71033    │ 1.077       │
│ 20  │ PET                             │ 5.5655     │ 3.5         │
│ 21  │ LC_Type4                        │ 3.16579    │ 1.0         │
│ 22  │ Evergreen_Needleleaf_Vegetation │ 0.56063    │ 0.0         │
│ 23  │ Evergreen_Broadleaf_Vegetation  │ 0.00825588 │ 0.0         │
│ 24  │ Deciduous_Needleleaf_Vegetation │ 0.0        │ 0.0         │
│ 25  │ Deciduous_Broadleaf_Vegetation  │ 0.0295039  │ 0.0         │
│ 26  │ Annual_Broadleaf_Vegetation     │ 0.0265127  │ 0.0         │
│ 27  │ Annual_Grass_Vegetation         │ 0.290666   │ 0.0         │
│ 28  │ Non_Vegetated_or_Builtup_Lands  │ 0.0844314  │ 0.0         │

In [8]:
Y_ord = convert(Matrix, data_cleaned[:, [:NDVI, :red_reflectance]]);
X_ord = dropzeros(sparse([fill(1.0, (N, 1)) convert(Matrix, data_cleaned[:, 28:28])]));

In [9]:
N

1020000

In [10]:
# priors #
K = 2; p = size(X_ord)[2]; q = size(Y_ord)[2];
μβ = fill(0.0, p, q); inv_Vr = spzeros(p, p);
μΛ = fill(0.0, K, q); inv_VΛ = spzeros(K, K);
νΣ = q + 1; ΨΣ = [[1.0 0.0]; [0.0 1.0]];
inv_Lr =  spzeros(p, p); Lμβ = inv_Lr * μβ;
inv_LΛ =  spzeros(K, K); LμΛ = inv_LΛ * μΛ;
aϕ = [200.0, 200.0]; bϕ = [4.0/200.0, 8.0/200.0];

In [11]:
# Some data preparations #
S1_ind = sort(setdiff(S_indx, hold_index_set["hold_ind1"]));        # S1 index
S2_ind = sort(setdiff(S_indx, hold_index_set["hold_ind2"]));        # S2 index
M1_ind = setdiff(S_indx, S1_ind);                                  # in S not in S1
M2_ind = setdiff(S_indx, S2_ind);                                  # in S not in S2 
obs_ind = vcat(S1_ind, S2_ind .+ N);              # index of the observed location for all response among N locations
perm_ind = sortperm(vcat(S1_ind, S2_ind));                    # the vector of the permutation 

v1 = zeros(N); v1[S1_ind] .= 1;
v2 = zeros(N); v2[S2_ind] .= 1;
index_S = (2^0 * v1 + 2^1 * v2);                              # build index indicating which response are observed
M1_Sind = findall(x -> x == 2^1, index_S[S_indx]);                 # index of M1 among S
M2_Sind = findall(x -> x == 2^0, index_S[S_indx]);                 # index of M2 among S

dim_invD = length(S1_ind) + length(S2_ind);
v12 = convert.(Int, v1 + v2);
v12_s = [x for x in v12 if x > 0];
nrep_ind = [x for i in v12 if i > 0 for x in repeat([i], i)];
invD_yind = [x for i in 1:length(nrep_ind) for x in repeat([perm_ind[i]], nrep_ind[i])];
invD_xind = Array{Float64}(undef, length(invD_yind));
indx_val = 1;
indx_pos = 1;
for i in 1:n
    indx = repeat(perm_ind[indx_val:(indx_val + v12_s[i] - 1)], v12_s[i]);
    invD_xind[indx_pos:(indx_pos + v12_s[i]^2 - 1)] = indx;
    indx_val = indx_val + v12_s[i];
    indx_pos = indx_pos + v12_s[i]^2;
end
Xtilde_indy_up = vcat(S_indx, S_indx .+ N);

In [12]:
# preallocation #

F_sam = Array{Float64,2}(undef, n , K);                           # preallocate the matrix F, store the F before burn-in 
μ_m1 = Array{Float64, 2}(undef, length(M1_ind), q);
μ_m2 = Array{Float64, 2}(undef, length(M2_ind), q);
nIndx = length(NN.nnIndx);
A = [Array{Float64}(undef, nIndx) for i in 1:K];
D = [Array{Float64}(undef, n) for i in 1:K];
I_A = [spzeros(n, n) for i in 1:K];
A_new = [Array{Float64}(undef, nIndx) for i in 1:K];
D_new = [Array{Float64}(undef, n) for i in 1:K];
I_A_new = [spzeros(n, n) for i in 1:K];
Ystar = vcat(Y_ord[S_indx, :], Lμβ, LμΛ);             # will be updated after imputing missing response 
Xstar = vcat([X_ord[S_indx, :] spzeros(n, K)], [inv_Lr spzeros(p, K)], [spzeros(K, p) inv_LΛ]);
Ψstar = fill(0.0, q, q); νstar = νΣ + n;
μγstar = vcat(μβ, μΛ); Vγstar = fill(0.0, p + K, p + K);
Y_Xm = fill(0.0, n, q); invVγstar = fill(0.0, p + K, p + K);
invD_ele = Array{Float64}(undef, length(invD_xind));
invD = SparseMatrixCSC{Float64,Int64};
nsam = length(perm_ind) + (K * n);
Ytilde =  Array{Float64}(undef, nsam);
Xtilde = SparseMatrixCSC{Float64,Int64};
precond_D = Array{Float64, 1}(undef, K * n);
Atilde = Array{Float64}(undef, NM * m); Dtilde = Array{Float64}(undef, NM);
lll = fill(1.0, (n, 1)); lllM = fill(1.0, (NM, 1));

MCMC sampling algorithm
Q1: priors for $\nu_i$ 
Q2: $\phi_i$ may not be consistant, since the order can change 

In [13]:
data_cleaned = nothing; hold_index_set = nothing; GC.gc();

In [14]:
Sys.free_memory()/(2^20*1024)

20.824325561523438

In [15]:
# Preallocation for MCMC samples and Initalization #
N_sam = 10000;
N_pre_burn = Integer(trunc(0.5 * N_sam));
N_pre_adapt = Integer(trunc(0.25 * N_sam));
N_after_burn = N_sam - N_pre_burn;
ω_incp_sam = Array{Float32, 2}(undef, n, q);
F_M_sam = Array{Float32, 2}(undef, NM, K);
ω_incp_M_sam = Array{Float32, 2}(undef, NM, q);
Y_M_sam = Array{Float32, 2}(undef, NM, q);

ω_incp_sam_mean = fill(0.0, n, q);
ω_incp_sam_var = fill(0.0, n, q);
Y_m1_sam_mean = fill(0.0, length(M1_ind));
Y_m1_sam_var = fill(0.0, length(M1_ind));
Y_m2_sam_mean = fill(0.0, length(M2_ind));
Y_m2_sam_var = fill(0.0, length(M2_ind));
ω_incp_M_sam_mean = fill(0.0, NM, q);
ω_incp_M_sam_var = fill(0.0, NM, q);
Y_M_sam_mean = fill(0.0, NM, q);
Y_M_sam_var = fill(0.0, NM, q);

A_sam = Array{Float64, 2}(undef, N_sam, K); # acceptance rate
lh_old = 1; lh_new = 1;     # record the likelihood for updating ranges

ϕ_sam = Array{Float64, 2}(undef, K, N_sam + 1);

γ_sam = vcat(fill(0.0, p, q), [[1.0 0.0]; [0.0 1.0]]);
Σ_sam = [[0.5 0.0]; [0.0 0.5]];
ω_cov_sam = [[0.5 0.0]; [0.0 0.5]];
ϕ_sam[:, 1] = [4.00, 8.00];

RWM_scale = [0.1, 0.1];                                              # random-walk metropolis step size scale 
# 0.2, 1.0
# 0.06, 0.5: 0.17 0.16
# 0.3 0.8: 0.024681346078268614 0.05

In [16]:
using DelimitedFiles
writedlm("../../results/BSLMC/γ_sam_nopredC.csv", vcat(fill(0.0, p + 1, q), [[1.0 0.0]; [0.0 1.0]]), ", ");
writedlm("../../results/BSLMC/Σ_sam_nopredC.csv", [[0.0 0.0]; [0.5 0.0]; [0.0 0.5]], ", ");
writedlm("../../results/BSLMC/ω_cov_sam_nopredC.csv", [[0.0 0.0]], ", ");
writedlm("../../results/BSLMC/ϕ_sam_nopredC.csv", vcat(0.0, ϕ_sam[:, 1]), ", ");
writedlm("../../results/BSLMC/A_sam_nopredC.csv", 0.0, ", ");

In [17]:
Sys.free_memory()/(2^20*1024)

20.80559539794922

In [18]:
# for loop for MCMC chain #
Random.seed!(1);
prog = Progress(N_sam, 1, "Computing initial pass...", 50)
for l in 1:N_sam
    # Build the matrix D_Sigma_o^{1/2} #
    Dic_diag = Dict(2^0 => (1 / sqrt(Σ_sam[1, 1])), 
        2^1 => (1 / sqrt(Σ_sam[2, 2])), 
        (2^0 + 2^1)=> (sqrt(inv(Σ_sam))));
    invD_ele = [x for i in index_S if i > 0 for x in Dic_diag[i]];
    invD = sparse(invD_xind, invD_yind, invD_ele);
                    
    # Build the matrix for the first iteration #
    if l == 1
@time   for i in 1:K
            getAD(coords, NN.nnIndx, NN.nnDist, NN.nnIndxLU, ϕ_sam[i], 0.5, A[i], D[i]);
            I_A[i] = sparse(nnIndx_row, nnIndx_col, vcat(-A[i], ones(n)));
        end
    end
                    

    # Build Ytilde Xtilde
    Ytilde = vcat(invD * vcat(Y_ord[S1_ind, 1] - X_ord[S1_ind, :] * γ_sam[1:p, 1], 
                            Y_ord[S2_ind, 2] - X_ord[S2_ind, :] * γ_sam[1:p, 2]), zeros(K * n));
@time    Xtilde = vcat(invD * kron(sparse(transpose(γ_sam[(p + 1):(p + K), :])), 
                            sparse(1:N, 1:N, ones(N)))[obs_ind, Xtilde_indy_up],
             blockdiag(Diagonal(1 ./ sqrt.(D[1])) * I_A[1], Diagonal(1 ./ sqrt.(D[2])) * I_A[2]));
    
    # use LSMR to generate sample of F #       
#    Precond_D = colnorm(Xtilde);
#@time    F_sam = reshape(Diagonal(1 ./ Precond_D) * lsmr(Xtilde * Diagonal(1 ./ Precond_D), 
#            collect(Ytilde) + rand(Normal(), nsam)), :, K);  
@time    F_sam = reshape(lsmr(Xtilde, collect(Ytilde) + rand(Normal(), nsam)), :, K);
    Xstar[1:n, (p + 1):(p + K)] = F_sam;        # update matrix Xstar with F
    
    if(l > N_pre_burn) # only save ω_incp_sam after burn-in
        ω_incp_sam = F_sam * γ_sam[(p + 1):(p + K), :] + lll * transpose(γ_sam[1, :]); 
        ω_incp_sam_mean = ω_incp_sam_mean + (ω_incp_sam ./ N_after_burn);
        ω_incp_sam_var = ω_incp_sam_var + (ω_incp_sam.^2 ./ N_after_burn);  
        ω_cov_sam = cov(ω_incp_sam);
    else
        ω_cov_sam = cov(F_sam * γ_sam[(p + 1):(p + K), :]);
    end                    
    io1 = open("../../results/BSLMC/ω_cov_sam_nopredC.csv", "a" ); # covariance of latent process
    writedlm(io1, ω_cov_sam, ", ");
    close(io1);

                    
    # impute missing response  over S#
    mul!(μ_m1, Xstar[M1_Sind, :], γ_sam);
    mul!(μ_m2, Xstar[M2_Sind, :], γ_sam);

    Y_m1_sam = μ_m1[:, 1] + (Σ_sam[1, 2] / Σ_sam[2, 2]) * 
         (Y_ord[M1_ind, 2] - μ_m1[:, 2]) + 
          rand(Normal(0, sqrt(Σ_sam[1, 1] - Σ_sam[1, 2]^2 / Σ_sam[2, 2])), length(M1_ind));
    Y_m2_sam = μ_m2[:, 2] + (Σ_sam[2, 1] / Σ_sam[1, 1]) * 
        (Y_ord[M2_ind, 1] - μ_m2[:, 1]) + 
        rand(Normal(0, sqrt(Σ_sam[2, 2] - Σ_sam[2, 1]^2 / Σ_sam[1, 1])), length(M2_ind)); # improve?...
                    
    if (l > N_pre_burn)  # only save imputed Y after burn-in
        Y_m1_sam_mean = Y_m1_sam_mean + (Y_m1_sam ./ N_after_burn);
        Y_m1_sam_var = Y_m1_sam_var + (Y_m1_sam.^2 ./ N_after_burn);
        Y_m2_sam_mean = Y_m2_sam_mean + (Y_m2_sam ./ N_after_burn);
        Y_m2_sam_var = Y_m2_sam_var + (Y_m2_sam.^2 ./ N_after_burn);
    end
    # use MNIW to sample γ Σ #
    Ystar[M1_Sind, 1] = Y_m1_sam;              # update Ystar with imputed response
    Ystar[M2_Sind, 2] = Y_m2_sam;               
                    
    invVγstar = cholesky(Xstar'Xstar);
    mul!(μγstar, transpose(Xstar), Ystar); μγstar = invVγstar.U \ (invVγstar.L \ μγstar);
    Y_Xm = Ystar - Xstar * μγstar;
    mul!(Ψstar, transpose(Y_Xm), Y_Xm); BLAS.axpy!(1.0, ΨΣ, Ψstar);

    Σ_sam = rand(InverseWishart(νstar, Ψstar), 1)[1];    # sample Σ
    γ_sam = (invVγstar.U \ reshape(rand(Normal(), (p + K) * q), (p + K), q)) *
                    cholesky(Σ_sam).U + μγstar;          # sample γ    
    io2 = open("../../results/BSLMC/Σ_sam_nopredC.csv", "a" );
    writedlm(io2, Σ_sam, ", ");
    close(io2); 
    io3 = open("../../results/BSLMC/γ_sam_nopredC.csv", "a" );
    writedlm(io3, γ_sam, ", ");
    close(io3);                 
    
    # use metropolis-hasting to update range
    if l > 3 && l < N_pre_adapt
        RWM_scale = [sqrt(2.38^2 * var(ϕ_sam[i, Integer(floor(l / 2)):l], corrected=true) * 0.95^2 + 0.05^2 * 0.1^2) for i in 1:K];
    end        
    ϕ_sam[:, l + 1] = [ϕ_sam[i, l] + RWM_scale[i] * rand(Normal(), 1)[1] for i in 1:K]; # propose next sample point 
@time for i in 1:K
        if ϕ_sam[i, l + 1] > 0.0
            lh_old = -0.5 * (sum(log.(D[i])) + norm((I_A[i] * F_sam[:, i]) ./ sqrt.(D[i]))^2 ) + 
               loglikelihood(Gamma(aϕ[i], bϕ[i]), [ϕ_sam[i, l]]);
            getAD(coords, NN.nnIndx, NN.nnDist, NN.nnIndxLU, ϕ_sam[i, l + 1], 0.5, A_new[i], D_new[i]);
            I_A_new[i] = sparse(nnIndx_row, nnIndx_col, vcat(-A_new[i], ones(n)));
            lh_new = -0.5 * (sum(log.(D_new[i]))  + norm((I_A_new[i] * F_sam[:, i]) ./ sqrt.(D_new[i]))^2) +
                    loglikelihood(Gamma(aϕ[i], bϕ[i]), [ϕ_sam[i, l + 1]]);     
            A_sam[l, i] = min(exp(lh_new - lh_old), 1.0);
            if rand(1)[1] < A_sam[l, i]
                I_A[i] = copy(I_A_new[i]); D[i] = copy(D_new[i]);        # update and update the corresponding I_A D
            else 
                ϕ_sam[i, l + 1] = ϕ_sam[i, l];
            end
        else 
            A_sam[l, i] = 0.0;
            ϕ_sam[:, l + 1] = ϕ_sam[:, l];   
        end
    end
    
    io4 = open("../../results/BSLMC/ϕ_sam_nopredC.csv", "a" );
    writedlm(io4, ϕ_sam[:, l + 1], ", ");
    close(io4); 
    io5 = open("../../results/BSLMC/A_sam_nopredC.csv", "a" );
    writedlm(io5, A_sam[l, :], ", ");
    close(io5)
                    
                    
    # Prediction:
    if(l > N_pre_burn) 
        for j in 1:K
            getAD(coords, MnnIndx, Mnndists, MnnIndxLU, ϕ_sam[j, l + 1], 0.5, Atilde, Dtilde);
            AtildeM = sparse(repeat(1:NM, inner = m), MnnIndx, Atilde, NM, n);
            F_M_sam[:, j] = AtildeM * F_sam[:, j] + sqrt.(Dtilde) .* rand(Normal(), NM);
        end
        ω_incp_M_sam = F_M_sam * γ_sam[(p + 1):(p + K), :] + lllM * transpose(γ_sam[1, :]);
        ω_incp_M_sam_mean = ω_incp_M_sam_mean + (ω_incp_M_sam ./ N_after_burn);
        ω_incp_M_sam_var = ω_incp_M_sam_var + (ω_incp_M_sam.^2 ./ N_after_burn);
        # update Y
        Y_M_sam = X_ord[U_indx, 2:p] * γ_sam[2:p, :] + ω_incp_M_sam + 
                        transpose(rand(MvNormal(Σ_sam), NM));
        Y_M_sam_mean = Y_M_sam_mean + (Y_M_sam ./ N_after_burn);
        Y_M_sam_var = Y_M_sam_var + (Y_M_sam.^2 ./ N_after_burn);            
    end

    next!(prog) # monitor the progress
end
ω_incp_sam_var = (ω_incp_sam_var - ω_incp_sam_mean.^2) * (N_after_burn / (N_after_burn - 1));
Y_m1_sam_var = (Y_m1_sam_var - Y_m1_sam_mean.^2) * (N_after_burn / (N_after_burn - 1));
Y_m2_sam_var = (Y_m2_sam_var - Y_m2_sam_mean.^2) * (N_after_burn / (N_after_burn - 1));
ω_incp_M_sam_var = (ω_incp_M_sam_var - ω_incp_M_sam_mean.^2) * (N_after_burn / (N_after_burn - 1));
Y_M_sam_var = (Y_M_sam_var - Y_M_sam_mean.^2) * (N_after_burn / (N_after_burn - 1)); 

  6.395016 seconds (37.71 M allocations: 10.364 GiB, 16.68% gc time)
  1.915354 seconds (2.05 M allocations: 1.669 GiB, 30.87% gc time)
 10.137983 seconds (2.41 M allocations: 2.013 GiB, 1.90% gc time)
  6.243601 seconds (36.47 M allocations: 10.599 GiB, 16.53% gc time)


Computing initial pass...  0%|                                                  |  ETA: 3 days, 17:09:02

  1.310466 seconds (154 allocations: 1.624 GiB, 50.58% gc time)
 18.544248 seconds (1.38 k allocations: 3.532 GiB, 2.56% gc time)


Computing initial pass...  0%|                                                  |  ETA: 3 days, 10:22:32

  5.915309 seconds (35.93 M allocations: 10.572 GiB, 15.84% gc time)
  1.283678 seconds (154 allocations: 1.624 GiB, 51.20% gc time)
 13.927997 seconds (1.04 k allocations: 2.685 GiB, 3.11% gc time)
 

...

Computing initial pass...100%|██████████████████████████████████████████████████|  ETA: 0:00:32

  1.465706 seconds (154 allocations: 1.624 GiB, 53.14% gc time)
  7.490294 seconds (394 allocations: 1.094 GiB, 6.45% gc time)
  6.390446 seconds (35.92 M allocations: 10.394 GiB, 20.62% gc time)


Computing initial pass...100%|██████████████████████████████████████████████████|  ETA: 0:00:16

  1.249170 seconds (154 allocations: 1.624 GiB, 49.93% gc time)
  5.953554 seconds (388 allocations: 1.079 GiB, 6.67% gc time)
  6.472886 seconds (35.92 M allocations: 10.394 GiB, 21.29% gc time)


Computing initial pass...100%|██████████████████████████████████████████████████| Time: 1 days, 20:44:45


In [19]:
RWM_scale

2-element Array{Float64,1}:
 0.0765003272462549 
 0.26236609230024366

In [20]:
@save "../../results/BSLMC/BSLMC_mean_var_nopredC.jld" ω_incp_sam_mean ω_incp_sam_var Y_m1_sam_mean Y_m1_sam_var Y_m2_sam_mean Y_m2_sam_var ω_incp_M_sam_mean ω_incp_M_sam_var Y_M_sam_mean Y_M_sam_var 

In [21]:
@save "../../results/BSLMC/BSLMC_sum_data_nopredC.jld" Y_ord S_indx U_indx M1_Sind M2_Sind M1_ind M2_ind K p q N_sam N_pre_burn NM